# 实验报告

## 运行环境：

操作系统：Ubuntu 16.04

程序语言：Python 3.6

框架：Pytorch 1.1.0

依赖包：

- Pytorch 1.1.0
- torchvision 0.3.0
- numpy 1.17.3
- tqdm 4.36.1

## 实验步骤

1. 读取数据集，使用 torchvision ImageFolder 读取并组织不同样本以及其对应的 label
2. 图片预处理，主要包括图片 Resize，RandomCrop，ToTensor，Normalize 等操作，其中使用左右 flip 图片来增强样本个数
3. 数据切分，使用 80% 的数据作为 training data，使用剩余的数据作为 test data，切分前数据随机进行排列
4. 设计网络，使用 vgg16 + MLP，最后通过 softmax 方法取最高概率的 label 作为预测结果，其中 loss 通过 cross entropy 进行计算
5. 设置优化器，尝试使用 SGD、Adam 作为优化器
6. 训练神经网络，并记录训练数据


## 实验结果

最佳分类准确率：72%

In [10]:
import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim
import torch.utils.data
from torchvision import datasets, transforms
import time
import os
import numpy as np
import torch.utils.data
import torchvision
from tqdm import tqdm


class Net(nn.Module):
    def __init__(self, args):
        super(Net, self).__init__()

        input_size = args['image_height'] * args['image_width']

        self.conv1 = nn.Conv2d(1, 32, 3)
        # self.conv2 = nn.Conv2d(16, 8, 3)
        self.maxpool = nn.MaxPool2d(2)
        self.dropout = nn.Dropout(0.3)
        # self.conv3 = nn.Conv2d(64, 128, 3)
        # self.conv4 = nn.Conv2d(128, 64, 3)
        # self.maxpool = nn.MaxPool2d(2)
        self.fc1 = nn.Linear(7200, 128)
        # self.fc2 = nn.Linear(1024, 512)
        self.fc3 = nn.Linear(128, 10)

    def forward(self, x, labels=None):
        x = torch.relu(self.conv1(x))
        # x = torch.relu(self.conv2(x))
        x = self.maxpool(x)
        x = self.dropout(x)
        # x = torch.relu(self.conv3(x))
        # x = torch.relu(self.conv4(x))
        x = x.flatten(start_dim=1)
        # print(x.shape)
        x = torch.relu(self.fc1(x))
        # x = torch.relu(self.fc2(x))
        x = torch.relu(self.fc3(x))

        outputs = (x,)

        if labels is not None:
            loss = F.cross_entropy(outputs[0], labels)
            outputs = (loss,) + outputs
        return outputs


class Net2(nn.Module):
    def __init__(self, args):
        super(Net2, self).__init__()

        self.input_size = args['image_height'] * args['image_width']
        self.fc1 = nn.Linear(self.input_size, 10)
        # self.fc2 = nn.Linear(500, 1000)
        # self.fc3 = nn.Linear(1000, 10)
        self.dropout = nn.Dropout(.3)

    def forward(self, x, labels=None):
        x = x.view(-1, self.input_size)
        x = torch.relu(self.fc1(x))
        # x = torch.sigmoid(self.fc2(x))
        # x = torch.sigmoid(self.fc3(x))
        # x = self.dropout(x)

        outputs = (x,)

        if labels is not None:
            loss = F.cross_entropy(outputs[0], labels)
            outputs = (loss,) + outputs
        return outputs


class Net3(nn.Module):
    def __init__(self, args):
        super(Net3, self).__init__()

        self.input_size = args['image_height'] * args['image_width']
        self.resnet = torchvision.models.resnet18()
        self.vgg16 = torchvision.models.vgg16()
        self.fc1 = nn.Linear(1000, 512)
        self.fc2 = nn.Linear(512, 10)
        self.dropout = nn.Dropout(.3)

    def forward(self, x, labels=None):
        x = self.vgg16(x)
        x = torch.relu(self.fc1(x))
        x = torch.relu(self.fc2(x))
        x = self.dropout(x)

        outputs = (x,)

        if labels is not None:
            loss = F.cross_entropy(outputs[0], labels)
            outputs = (loss,) + outputs
        return outputs


def train(model, train_data, optimizer):
    model.train()
    pbar = tqdm(train_data)

    correct = 0
    count = 0
    train_loss = 0

    for step, (x, y) in enumerate(pbar):
        x, y = x.to(device), y.to(device)
        optimizer.zero_grad()
        outputs = model(x, labels=y)
        loss = outputs[0]
        loss.backward()
        optimizer.step()

        # 得到预测结果
        pred = outputs[1].softmax(dim=1).argmax(dim=1, keepdim=True)
        # print(outputs[1].softmax(dim=1))
        # 计算正确个数
        correct += pred.eq(y.view_as(pred)).sum().item()
        count += len(x)
        train_loss += loss.item()
        pbar.set_postfix({
            'loss': '{:.3f}'.format(loss.item()),
            'acc': '{:.3f}'.format(correct * 1.0 / count)
        })
    return train_loss / count, correct * 1.0 / count


def test(model, test_data):
    model.eval()
    test_loss = 0
    correct = 0
    count = 0
    for step, (x, y) in enumerate(test_data):
        x, y = x.to(device), y.to(device)
        outputs = model(x, labels=y)
        test_loss += outputs[0].item()
        pred = outputs[1].softmax(dim=1).argmax(dim=1, keepdim=True)
        correct += pred.eq(y.view_as(pred)).sum().item()
        count += len(x)
    test_loss /= count
    print(
        '\nTest set: Average loss: {:.4f}, Accuracy: {}/{} ({:.4f}%)\n'.format(
            test_loss, correct, count, 100. * correct / count))
    return test_loss, correct * 1.0 / count


if __name__ == '__main__':
    args = {
        'batch_size': 32,
        'test_batch_size': 32,
        'lr': 0.01,
        'epochs': 300,
        'use_cuda': torch.cuda.is_available(),
        'data_loader_num_workers': 1,
        'split_rate': 0.8,
        'image_height': 64,
        'image_width': 64,
    }

    device = torch.device('cuda' if args['use_cuda'] else 'cpu')
    kwargs = {'num_workers': args['data_loader_num_workers'], 'pin_memory': True} if args['use_cuda'] else {}

    image_data = torchvision.datasets.ImageFolder('face', transform=transforms.Compose([
        # transforms.Grayscale(num_output_channels=1),
        transforms.Resize((args['image_height'] + 0, args['image_width'] + 0)),
        # transforms.RandomCrop((args['image_height'], args['image_width'])),
        transforms.ToTensor(),
        transforms.Normalize((0.1307,), (0.3081,)),
    ]))
    image_data = list(image_data)
    tmp = image_data.copy()
    image_data.extend([(i[0].flip(1), i[1]) for i in tmp])

    data_loader = torch.utils.data.DataLoader(dataset=image_data,
                                              batch_size=args['batch_size'],
                                              shuffle=True,
                                              **kwargs,
                                              )
    data_loader = list(data_loader)
    train_data = data_loader[:int(len(data_loader) * args['split_rate'])]
    test_data = data_loader[int(len(data_loader) * args['split_rate']):]

    model = Net3(args).to(device)
    optimizer = optim.SGD(model.parameters(), lr=args['lr'])

    start_time = time.time()
    for epoch in range(args['epochs']):
        print('Epoch {}/{}'.format(epoch + 1, args['epochs']))
        train(model, train_data, optimizer)
        test(model, test_data)
    print('Total Time: ', time.time() - start_time)








  0%|          | 0/67 [00:00<?, ?it/s]






  0%|          | 0/67 [00:00<?, ?it/s, loss=2.298, acc=0.250]






  0%|          | 0/67 [00:00<?, ?it/s, loss=2.293, acc=0.250]






  0%|          | 0/67 [00:00<?, ?it/s, loss=2.302, acc=0.198]






  4%|▍         | 3/67 [00:00<00:02, 26.01it/s, loss=2.302, acc=0.198]





 66%|██████▌   | 44/67 [00:11<00:00, 36.26it/s, loss=2.262, acc=0.178]






  4%|▍         | 3/67 [00:00<00:02, 26.01it/s, loss=2.305, acc=0.172]






  4%|▍         | 3/67 [00:00<00:02, 26.01it/s, loss=2.291, acc=0.181]

Epoch 1/300









  4%|▍         | 3/67 [00:00<00:02, 26.01it/s, loss=2.282, acc=0.193]






  9%|▉         | 6/67 [00:00<00:02, 25.67it/s, loss=2.282, acc=0.193]






  9%|▉         | 6/67 [00:00<00:02, 25.67it/s, loss=2.304, acc=0.179]






  9%|▉         | 6/67 [00:00<00:02, 25.67it/s, loss=2.292, acc=0.176]






  9%|▉         | 6/67 [00:00<00:02, 25.67it/s, loss=2.279, acc=0.184]






 13%|█▎        | 9/67 [00:00<00:02, 25.94it/s, loss=2.279, acc=0.184]






 13%|█▎        | 9/67 [00:00<00:02, 25.94it/s, loss=2.295, acc=0.181]






 13%|█▎        | 9/67 [00:00<00:02, 25.94it/s, loss=2.263, acc=0.193]






 13%|█▎        | 9/67 [00:00<00:02, 25.94it/s, loss=2.290, acc=0.188]






 18%|█▊        | 12/67 [00:00<00:02, 26.20it/s, loss=2.290, acc=0.188]






 18%|█▊        | 12/67 [00:00<00:02, 26.20it/s, loss=2.275, acc=0.190]






 18%|█▊        | 12/67 [00:00<00:02, 26.20it/s, loss=2.278, acc=0.188]






 18%|█▊        | 12/67 [00:00<00:02, 26.20it/s, loss=2.258, acc=0.194]






 

  0%|          | 0/67 [00:00<?, ?it/s, loss=2.120, acc=0.312]






  0%|          | 0/67 [00:00<?, ?it/s, loss=2.285, acc=0.250]






  0%|          | 0/67 [00:00<?, ?it/s, loss=2.338, acc=0.229]






  4%|▍         | 3/67 [00:00<00:02, 27.13it/s, loss=2.338, acc=0.229]






  4%|▍         | 3/67 [00:00<00:02, 27.13it/s, loss=2.317, acc=0.195]






  4%|▍         | 3/67 [00:00<00:02, 27.13it/s, loss=2.218, acc=0.200]


Test set: Average loss: 0.0701, Accuracy: 118/540 (21.8519%)

Epoch 2/300


...








  4%|▍         | 3/67 [00:00<00:02, 26.16it/s, loss=0.720, acc=0.693]






  9%|▉         | 6/67 [00:00<00:02, 26.13it/s, loss=0.720, acc=0.693]






  9%|▉         | 6/67 [00:00<00:02, 26.13it/s, loss=0.936, acc=0.688]






  9%|▉         | 6/67 [00:00<00:02, 26.13it/s, loss=0.720, acc=0.688]






  9%|▉         | 6/67 [00:00<00:02, 26.13it/s, loss=0.648, acc=0.705]






 13%|█▎        | 9/67 [00:00<00:02, 26.15it/s, loss=0.648, acc=0.705]






 13%|█▎        | 9/67 [00:00<00:02, 26.15it/s, loss=0.792, acc=0.703]






 13%|█▎        | 9/67 [00:00<00:02, 26.15it/s, loss=0.792, acc=0.707]






 13%|█▎        | 9/67 [00:00<00:02, 26.15it/s, loss=0.576, acc=0.711]






 18%|█▊        | 12/67 [00:00<00:02, 26.09it/s, loss=0.576, acc=0.711]






 18%|█▊        | 12/67 [00:00<00:02, 26.09it/s, loss=0.792, acc=0.716]






 18%|█▊        | 12/67 [00:00<00:02, 26.09it/s, loss=0.935, acc=0.712]






 18%|█▊        | 12/67 [00:00<00:02, 26.09it/s, loss=0.935, acc=0.706]






 

  0%|          | 0/67 [00:00<?, ?it/s, loss=0.504, acc=0.844]






  0%|          | 0/67 [00:00<?, ?it/s, loss=0.935, acc=0.719]






  0%|          | 0/67 [00:00<?, ?it/s, loss=1.151, acc=0.656]






  4%|▍         | 3/67 [00:00<00:02, 26.96it/s, loss=1.151, acc=0.656]






  4%|▍         | 3/67 [00:00<00:02, 26.96it/s, loss=1.007, acc=0.648]






  4%|▍         | 3/67 [00:00<00:02, 26.96it/s, loss=0.504, acc=0.681]


Test set: Average loss: 0.0561, Accuracy: 346/540 (64.0741%)

Epoch 300/300









  4%|▍         | 3/67 [00:00<00:02, 26.96it/s, loss=0.648, acc=0.688]






  9%|▉         | 6/67 [00:00<00:02, 26.93it/s, loss=0.648, acc=0.688]






  9%|▉         | 6/67 [00:00<00:02, 26.93it/s, loss=0.432, acc=0.705]






  9%|▉         | 6/67 [00:00<00:02, 26.93it/s, loss=0.576, acc=0.715]






  9%|▉         | 6/67 [00:00<00:02, 26.93it/s, loss=0.648, acc=0.729]






 13%|█▎        | 9/67 [00:00<00:02, 26.95it/s, loss=0.648, acc=0.729]






 13%|█▎        | 9/67 [00:00<00:02, 26.95it/s, loss=0.863, acc=0.722]






 13%|█▎        | 9/67 [00:00<00:02, 26.95it/s, loss=0.360, acc=0.739]






 13%|█▎        | 9/67 [00:00<00:02, 26.95it/s, loss=0.720, acc=0.734]






 18%|█▊        | 12/67 [00:00<00:02, 26.94it/s, loss=0.720, acc=0.734]






 18%|█▊        | 12/67 [00:00<00:02, 26.94it/s, loss=0.935, acc=0.731]






 18%|█▊        | 12/67 [00:00<00:02, 26.94it/s, loss=1.439, acc=0.721]






 18%|█▊        | 12/67 [00:00<00:02, 26.94it/s, loss=0.648, acc=0.725]






 


Test set: Average loss: 0.0564, Accuracy: 347/540 (64.2593%)

Total Time:  812.9573032855988
